In [ ]:
! pip install fuzzywuzzy

In [3]:
import pandas as pd 
import numpy as np
from fuzzywuzzy import fuzz
from tqdm import tqdm
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
import re
from collections import Counter

import warnings
warnings.filterwarnings('ignore')

/Users/jerry/opt/anaconda3/lib/python3.8/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
stanford_cleand = pd.read_csv('drive-download-20220516T014219Z-001/final_reformatted_stanford.csv')
patent_data = pd.read_csv('drive-download-20220516T014219Z-001/complete_grouped.csv') 

# some more data cleaning and string processing work

In [3]:
# some low key data preprocesing

# lowercase patent_data
stanford_cleand.Infringer = stanford_cleand.Infringer.str.lower()
patent_data.correspondence_name = patent_data.correspondence_name.str.lower()

# remove all commas
stanford_cleand.Infringer = stanford_cleand.Infringer.apply(lambda x : x.replace(',',''))
patent_data.correspondence_name = patent_data.correspondence_name.apply(lambda x : x.replace(',',''))


# remove some specifics endings 
stanford_cleand.Infringer = stanford_cleand.Infringer.apply(lambda x: re.sub(r"\W(inc|llc|corp|ltd|co|ltd|lp)\b", "", x))
patent_data.correspondence_name = patent_data.correspondence_name.apply(lambda x: re.sub(r"\W(inc|llc|corp|ltd|co|ltd|lp)\b", "", x))

# stripping leading and trailing white spaces; and apply lower case to all names
stanford_cleand.Infringer = stanford_cleand.Infringer.replace(r"^ +| +$", r"", regex=True)
patent_data.correspondence_name = patent_data.correspondence_name.replace(r"^ +| +$", r"", regex=True)

In [4]:
stanford_cleand

Unnamed: 0      Infringer  Year  troll  sued  troll indic  \
0                 0   #1 wholesale  2000    0.0   0.0            0   
1                 1   #1 wholesale  2001    0.0   0.0            0   
2                 2   #1 wholesale  2002    0.0   0.0            0   
3                 3   #1 wholesale  2003    0.0   0.0            0   
4                 4   #1 wholesale  2004    0.0   0.0            0   
...             ...            ...   ...    ...   ...          ...   
1605269     1605269  zzounds music  2017    0.0   1.0            0   
1605270     1605270  zzounds music  2018    0.0   1.0            0   
1605271     1605271  zzounds music  2019    0.0   1.0            0   
1605272     1605272  zzounds music  2020    0.0   1.0            0   
1605273     1605273  zzounds music  2021    0.0   1.0            0   

         sued indic  first trolled  first sued  
0                 0            NaN        2016  
1                 0            NaN        2016  
2                 0            NaN        2016  
3                 0            NaN        2016  
4                 0            NaN        2016  
...             ...            ...         ...  
1605269           1            NaN        2015  
1605270           1            NaN        2015  
1605271           1            NaN        2015  
1605272           1            NaN        2015  
1605273           1            NaN        2015  

[1605274 rows x 9 columns]

# Our goal: our goal is to create a mapping of company names. A mapping from each unique patent company to a infringer  (if exists). 

## Once we obtain the mapping, we can apply the mapping to our patent dataset then we can do a brute force merging between patent and infringer dataset

In [5]:
unique_infringers = stanford_cleand.Infringer.unique()
unique_patent_co  = patent_data.correspondence_name.unique()
print("unique infringers", len(unique_infringers))
print("unique patent owners",len(unique_patent_co))

unique infringers 72881
unique patent owners 364318


In [6]:
# return a match if there is a match that has a fuzzy score above min_score = 70
# return empty and -1 if there is no such match

def match_name(name, list_names, min_score=70):
    # -1 score incase we don't get any matches
    max_score = -1
    # Returning empty name for no match as well
    max_name = ""
    # Iternating over all names in the other
    for name2 in list_names:
        #Finding fuzzy match score
        score = fuzz.ratio(name, name2)
        # Checking if we are above our threshold and have a better score
        if (score > min_score) & (score > max_score):
            max_name = name2
            max_score = score
    return (max_name, max_score)


In [ ]:
process.extract("trevor", unique_infringers)

In [7]:
# test 1
match_name("juniper networks", unique_infringers, 70)

('juniper networks', 100)

In [ ]:
# test 2
match_name("amazon", unique_patent_co, 80)[1]

In [8]:
Str1 = "Trevor Technologies"
Str2 = "Grace Investment"
Ratio = fuzz.ratio(Str1.lower(),Str2.lower())
print(Ratio)

29


# Prepartory work setting up the dataframe

In [9]:
your_part = unique_patent_co # set it to your designated part

In [10]:
test_match = pd.DataFrame(your_part, columns = ["patent_co"])
test_match["best_match"] = ""
test_match["best_score"] = 0 
test_match

patent_co best_match  best_score
0            & bicknell attn: d j brott                      0
1            & glaser att: l dan tucker                      0
2        & glaser attn: dennis t griggs                      0
3       & glaser attn: e mickey hubbard                      0
4       & glaser attn: kenneth r glaser                      0
...                                 ...        ...         ...
364313               ãngel pons ariã±o                      0
364314      ãvoã wine technologies sa                      0
364315                     ãgon design                      0
364316                    ãgon designs                      0
364317                     ãyvind berg                      0

[364318 rows x 3 columns]

# Establish subgroups for Mapping

In [13]:
# we divide uniqnue patent company into subgroups by first two characters of the patent comapny name
unique_infringer_df = pd.DataFrame(unique_infringers, columns = ['infringers'])
unique_infringer_df['sort_gp'] = unique_infringer_df['infringers'].apply(lambda x: x[:2])
all_sort_gp = unique_infringer_df['sort_gp'].unique()

print("all sub group")
for i in all_sort_gp:
  print(i)
print("total number of sub group start with first two characters" , len(all_sort_gp))


all sub group
#1
&q
(f
(u
#n
/ 
01
02
07
74
1
1 
1&
1-
10
11
12
13
14
15
16
17
18
19
1a
1b
1k
1r
1s
1t
2 
20
21
22
23
24
28
2c
2d
2g
2i
2k
2m
2n
2p
2s
2t
2w
2x
3 
3-
30
31
32
33
35
36
3a
3b
3c
3d
3e
3f
3j
3l
3m
3n
3o
3p
3r
3s
3t
3v
3w
3x
4 
40
41
43
44
45
48
49
4b
4c
4d
4e
4i
4k
4p
4q
4s
4t
50
51
52
54
55
56
58
5_
5b
5s
5t
6/
60
61
64
66
67
69
6h
6s
6w
7-
71
72
77
7c
7d
7f
7h
7p
7t
8 
80
83
85
86
88
8x
90
91
92
95
98
99
9x
:o
@r
a 
a&
a'
a+
a-
a/
a1
a2
a4
a7
a9
a_
aa
ab
ac
ad
ae
af
ag
ah
ai
aj
ak
al
am
an
ao
ap
aq
ar
as
at
au
av
aw
ax
ay
az
b 
b&
b*
b+
b-
b/
b2
b4
b8
ba
bb
bc
bd
be
bf
bg
bh
bi
bj
bk
bl
bm
bn
bo
bp
br
bs
bt
bu
bv
bw
by
bz
c
c 
c&
c-
c/
c1
c2
c3
c4
ca
cb
cc
cd
ce
cf
cg
ch
ci
cj
ck
cl
cm
cn
co
cp
cq
cr
cs
ct
cu
cv
cw
cx
cy
d 
d&
d'
d-
d/
d2
d3
d4
d6
da
db
dc
dd
de
df
dg
dh
di
dj
dk
dl
dm
dn
do
dp
dq
dr
ds
dt
du
dv
dw
dx
dy
dz
e 
e&
e'
e*
e-
e2
e4
e_
ea
eb
ec
ed
ee
ef
eg
eh
ei
ej
ek
el
em
en
eo
ep
eq
er
es
et
eu
ev
ew
ex
ey
ez
f
f 
f&
f-
f3
f4
f5
f_
fa
fb
fc
fd
fe
ff
fg
fh

In [14]:
unique_infringer_df

infringers sort_gp
0              #1 wholesale      #1
1                     &quot      &q
2           (f/n/u) ramirez      (f
3                     (usa)      (u
4                    #name?      #n
...                     ...     ...
72876                zyppah      zy
72877                 zyvex      zy
72878  zyxel communications      zy
72879        zyxel networks      zy
72880         zzounds music      zz

[72881 rows x 2 columns]

In [25]:
# go through each individual infringer and look for the best match of patent company
good_match = 0 
for i in tqdm(range(len(test_match))):
# for i in tqdm(range(0,1000)):
    current_target = test_match.iloc[i]["patent_co"]
    first_2letter = current_target[:2]
    # print(first_2letter)

    # if the first two letters matches one of the groups we created ealier, then we proceed to forward
    if first_2letter in all_sort_gp:
        
        candidate_list = unique_infringer_df.groupby(['sort_gp']).get_group(first_2letter)['infringers'].tolist()
        # print(len(candidate_list))
        temp = match_name(current_target, candidate_list, 80)
        
        test_match.at[i, "best_match"] = temp[0]
        test_match.at[i, "best_score"] = temp[1]
#         if temp[1] != -1:
#             good_match = good_match+1
#             print("target", current_target)
#             print("best_match", temp[0])
#             print("score", temp[1])


  1%|          | 3044/364318 [00:31<1:52:28, 53.53it/s]


  1%|▏         | 4971/364318 [01:06<3:32:31, 28.18it/s]


  2%|▏         | 5984/364318 [01:40<3:27:40, 28.76it/s]


  2%|▏         | 6945/364318 [02:13<3:47:49, 26.14it/s]


  2%|▏         | 7862/364318 [02:46<3:15:51, 30.33it/s]


...

 97%|█████████▋| 355018/364318 [2:16:38<03:18, 46.82it/s]


 98%|█████████▊| 356412/364318 [2:17:07<02:49, 46.73it/s]


 98%|█████████▊| 357803/364318 [2:17:37<02:32, 42.84it/s]


 99%|█████████▉| 360146/364318 [2:18:08<00:21, 196.74it/s]


100%|██████████| 364318/364318 [2:18:36<00:00, 43.81it/s] 


## this step, we read the mapping, this mapping from patent company to infringer has been manually adjusted 

In [6]:
# reading the match: 
test_match = pd.read_csv("mapping_alternative_manul.csv")

In [40]:
# test_match.to_csv('mapping_2.csv')  

In [7]:
test_match.head()

Unnamed: 0              patent_co             best_match  best_score
0         151           10x genomics           10x genomics         100
1         168  12 sigma technologies  12 sigma technologies         100
2         309           2go products           2go products         100
3         381                   3com                   3com         100
4         385             3d systems             3d systems         100

In [8]:
test_match.shape

(364318, 4)

## Split into valid match (certain, in a sense that the socre is very high )

In [9]:
certain_match = test_match.loc[test_match['best_score'] >= 91]

In [10]:
print(certain_match.shape)

(8932, 4)


## Split into valid no match ( certain , in a sense that the score is bad)

In [11]:
certain_no_match = test_match.loc[test_match['best_score'] < 80]

In [12]:
print(certain_no_match.shape)

(328711, 4)


## Drop the uncertains mapping (the score falls in between.) 

In [13]:
uncertain = test_match.loc[(test_match['best_score'] < 91) & (test_match['best_score']>= 80)]

In [14]:
uncertain.shape

(26675, 4)

In [15]:
uncertain.head(5)

Unnamed: 0                    patent_co                best_match  \
8932        2055              abs partnership          abc partnerships   
8933        2261               acuity systems         actuality systems   
8934        3277         advance applications      advance publications   
8935        3331  advanced fiber technologies  advanced rf technologies   
8936        3337  advanced green technologies  advanced rf technologies   

      best_score  
8932          90  
8933          90  
8934          90  
8935          90  
8936          90

In [16]:
uncertain_list = uncertain.patent_co.tolist()

## Concatenate the certian ones: 

In [17]:
certainty = pd.concat([certain_match, certain_no_match])

In [18]:
certainty.shape

(337643, 4)

In [19]:
certainty.head(4)

Unnamed: 0              patent_co             best_match  best_score
0         151           10x genomics           10x genomics         100
1         168  12 sigma technologies  12 sigma technologies         100
2         309           2go products           2go products         100
3         381                   3com                   3com         100

In [20]:
dict_match = certainty.set_index('patent_co').to_dict()['best_match']

In [21]:
len(dict_match)

337636

# Now drop the uncertained matches so that we only have certained match and certained no-match left

In [22]:
patent_data_copy = patent_data.copy()


In [23]:
patent_data_copy['original_name'] = patent_data_copy['correspondence_name'] 

In [24]:
patent_data_copy.head(3)

Unnamed: 0         correspondence_name  Year  patents     industry  \
0          22  & bicknell attn: d j brott  2000      0.0  Health Care   
1          23  & bicknell attn: d j brott  2001      0.0  Health Care   
2          24  & bicknell attn: d j brott  2002      0.0  Health Care   

                original_name  
0  & bicknell attn: d j brott  
1  & bicknell attn: d j brott  
2  & bicknell attn: d j brott

In [25]:
patent_data_copy.shape

(8478668, 6)

In [26]:
# drop rows of uncertain matches  from a list of value
patent_data_copy = patent_data_copy[~patent_data_copy.correspondence_name.isin(uncertain_list)]

In [27]:
patent_data_copy.shape

(7875912, 6)

In [28]:
len(set(patent_data_copy.correspondence_name.tolist()))

337643

In [29]:
patent_data_copy.loc[patent_data_copy['correspondence_name'] == "10x genomics"]

Unnamed: 0 correspondence_name  Year  patents   industry original_name
3322        3344        10x genomics  2000      0.0  Materials  10x genomics
3323        3345        10x genomics  2001      0.0  Materials  10x genomics
3324        3346        10x genomics  2002      0.0  Materials  10x genomics
3325        3347        10x genomics  2003      0.0  Materials  10x genomics
3326        3348        10x genomics  2004      0.0  Materials  10x genomics
3327        3349        10x genomics  2005      0.0  Materials  10x genomics
3328        3350        10x genomics  2006      0.0  Materials  10x genomics
3329        3351        10x genomics  2007      0.0  Materials  10x genomics
3330        3352        10x genomics  2008      0.0  Materials  10x genomics
3331        3353        10x genomics  2009      0.0  Materials  10x genomics
3332        3354        10x genomics  2010      0.0  Materials  10x genomics
3333        3355        10x genomics  2011      0.0  Materials  10x genomics
3334        3356        10x genomics  2012      0.0  Materials  10x genomics
3335        3357        10x genomics  2013      0.0  Materials  10x genomics
3336        3358        10x genomics  2014      0.0  Materials  10x genomics
3337        3359        10x genomics  2015      0.0  Materials  10x genomics
3338        3360        10x genomics  2016      0.0  Materials  10x genomics
3339        3361        10x genomics  2017      0.0  Materials  10x genomics
3340        3362        10x genomics  2018      0.0  Materials  10x genomics
3341        3363        10x genomics  2019      0.0  Materials  10x genomics
3342        3364        10x genomics  2020      0.0  Materials  10x genomics
3343        3365        10x genomics  2021      0.0  Materials  10x genomics

In [30]:
dict_match

{'10x genomics': '10x genomics',
 '12 sigma technologies': '12 sigma technologies',
 '2go products': '2go products',
 '3com': '3com',
 '3d systems': '3d systems',
 '3m': '3m',
 '3m innovative properties': '3m innovative properties',
 '5th axis': '5th axis',
 '745': '745',
 'a b dick': 'a b dick',
 'a delaware': 'a delaware',
 'a&j manufacturing': 'a&j manufacturing',
 'aacer flooring': 'aacer flooring',
 'aaron f barkoff': 'aaron f barkoff',
 'aaron k alexander': 'aaron k alexander',
 'ab volvo': 'ab volvo',
 'abb': 'abb',
 'abba optical': 'abba optical',
 'abbas ben afshari': 'abbas ben afshari',
 'abbott bioresearch center': 'abbott bioresearch center',
 'abbott diabetes care': 'abbott diabetes care',
 'abbott laboratories': 'abbott laboratories',
 'abbott medical optics': 'abbott medical optics',
 'abbott molecular': 'abbott molecular',
 'abbott vascular': 'abbott vascular',
 'abbvie': 'abbvie',
 'abbyy usa': 'abbyy usa',
 'abgent': 'abgent',
 'ablation frontiers': 'ablation frontie

# now apply the mapping to patent dataset (certain matches + certain no matches) 

In [31]:
patent_data_copy['correspondence_name']= patent_data_copy['correspondence_name'].map(dict_match).fillna(patent_data_copy['correspondence_name'])

In [32]:
patent_data_copy.shape

(7875912, 6)

In [33]:
patent_data_copy['correspondence_name'].isna().sum()

0

# Now merge patent data with infringer data

In [34]:
stanford_cleand.head(3)

Unnamed: 0     Infringer  Year  troll  sued  troll indic  sued indic  \
0           0  #1 wholesale  2000    0.0   0.0            0           0   
1           1  #1 wholesale  2001    0.0   0.0            0           0   
2           2  #1 wholesale  2002    0.0   0.0            0           0   

   first trolled  first sued  
0            NaN        2016  
1            NaN        2016  
2            NaN        2016

## Left join, so patent data stays the way it is , infringer (stanford join left direction)

In [35]:
# stanford_cleand_copy is after appply fuzzy wuzzy mapping on the stanford dataset
lit_df = patent_data_copy.merge(stanford_cleand, how='left', left_on=['correspondence_name', 'Year'], 
                                right_on=['Infringer', 'Year'])

# lit_df.dropna(subset=['correspondence_name'], inplace=True)


In [36]:
lit_df.head(3)

Unnamed: 0_x         correspondence_name  Year  patents     industry  \
0            22  & bicknell attn: d j brott  2000      0.0  Health Care   
1            23  & bicknell attn: d j brott  2001      0.0  Health Care   
2            24  & bicknell attn: d j brott  2002      0.0  Health Care   

                original_name  Unnamed: 0_y Infringer  troll  sued  \
0  & bicknell attn: d j brott           NaN       NaN    NaN   NaN   
1  & bicknell attn: d j brott           NaN       NaN    NaN   NaN   
2  & bicknell attn: d j brott           NaN       NaN    NaN   NaN   

   troll indic  sued indic  first trolled  first sued  
0          NaN         NaN            NaN         NaN  
1          NaN         NaN            NaN         NaN  
2          NaN         NaN            NaN         NaN

In [37]:
lit_df.shape

(7876374, 14)

In [38]:
lit_df.dropna(subset=['correspondence_name'], inplace=True)

In [39]:
lit_df.shape

(7876374, 14)

In [40]:
print(len(lit_df['correspondence_name'].unique()))

333567


## Measure the succesful merge

In [41]:
print(len(lit_df['Infringer'].unique()))

4857


In [42]:
print(len(lit_df.dropna(subset=['Infringer'])['correspondence_name'].unique()))

4856


# Now read the processed public  info and do the second merge

In [44]:
public = pd.read_csv('company_size_and_research_fuzzy_matched.csv')

In [45]:
len(lit_df.correspondence_name.unique())

333567

In [46]:
len(public.Company.unique())

27672

In [47]:
lit_df.head(1)

Unnamed: 0_x         correspondence_name  Year  patents     industry  \
0            22  & bicknell attn: d j brott  2000      0.0  Health Care   

                original_name  Unnamed: 0_y Infringer  troll  sued  \
0  & bicknell attn: d j brott           NaN       NaN    NaN   NaN   

   troll indic  sued indic  first trolled  first sued  
0          NaN         NaN            NaN         NaN

In [48]:
public.head(1)

Unnamed: 0.1  Unnamed: 0                   Company  Year Currency  \
0             0           0  01 communique laboratory  2000      CAD   

   Total Assets (millions)  Employees (thousands) Company Status  \
0                   20.226                    NaN              A   

   Market Cap (millions) State Incorporated  ...   fyear indfmt  consol  \
0               168.4491                NaN  ...  2000.0   INDL       C   

   popsrc  datafmt    tic                      conm curcd    xrd costat  
0       D      STD  OONEF  01 communique laboratory   CAD  1.561      A  

[1 rows x 26 columns]

In [49]:
full_lit_df = lit_df.merge(public, how='left', left_on=['original_name', 'Year'], 
                                right_on=['Company', 'Year'])
print(len(full_lit_df['correspondence_name'].unique()))

333567


In [1]:
full_lit_df.head()

NameError: name 'full_lit_df' is not defined

In [50]:
full_lit_df.Infringer.unique()

array([nan, '10x genomics', '12 sigma technologies', ..., 'zte (usa)',
       'zymogenetics', 'zyvex'], dtype=object)

In [51]:
print(len(full_lit_df['Company'].unique()))

1059


In [54]:
full_lit_df.head(3)

Unnamed: 0_x         correspondence_name  Year  patents     industry  \
0            22  & bicknell attn: d j brott  2000      0.0  Health Care   
1            23  & bicknell attn: d j brott  2001      0.0  Health Care   
2            24  & bicknell attn: d j brott  2002      0.0  Health Care   

                original_name  Unnamed: 0_y Infringer  troll  sued  ...  \
0  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   
1  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   
2  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   

   fyear  indfmt  consol  popsrc  datafmt  tic conm curcd  xrd  costat  
0    NaN     NaN     NaN     NaN      NaN  NaN  NaN   NaN  NaN     NaN  
1    NaN     NaN     NaN     NaN      NaN  NaN  NaN   NaN  NaN     NaN  
2    NaN     NaN     NaN     NaN      NaN  NaN  NaN   NaN  NaN     NaN  

[3 rows x 39 columns]

In [56]:
full_lit_df.columns

Index(['Unnamed: 0_x', 'correspondence_name', 'Year', 'patents', 'industry',
       'original_name', 'Unnamed: 0_y', 'Infringer', 'troll', 'sued',
       'troll indic', 'sued indic', 'first trolled', 'first sued',
       'Unnamed: 0.1', 'Unnamed: 0', 'Company', 'Currency',
       'Total Assets (millions)', 'Employees (thousands)', 'Company Status',
       'Market Cap (millions)', 'State Incorporated', 'S&P industry code',
       'State', 'Public', 'Always Public', 'gvkey', 'datadate', 'fyear',
       'indfmt', 'consol', 'popsrc', 'datafmt', 'tic', 'conm', 'curcd', 'xrd',
       'costat'],
      dtype='object')

In [57]:
# drop unecassry columns
full_lit_df = full_lit_df.drop(columns=['Unnamed: 0_x', 'Unnamed: 0_y', 'Unnamed: 0.1', 'Unnamed: 0'])

In [58]:
full_lit_df.columns


Index(['correspondence_name', 'Year', 'patents', 'industry', 'original_name',
       'Infringer', 'troll', 'sued', 'troll indic', 'sued indic',
       'first trolled', 'first sued', 'Company', 'Currency',
       'Total Assets (millions)', 'Employees (thousands)', 'Company Status',
       'Market Cap (millions)', 'State Incorporated', 'S&P industry code',
       'State', 'Public', 'Always Public', 'gvkey', 'datadate', 'fyear',
       'indfmt', 'consol', 'popsrc', 'datafmt', 'tic', 'conm', 'curcd', 'xrd',
       'costat'],
      dtype='object')

In [59]:
print("fully_merged_with_certainties_also_updated_with_r_and_d_latest")
full_lit_df.to_csv("final_merged_all_three.csv")

fully_merged_with_certainties_also_updated_with_r_and_d_latest


In [160]:

full_lit_df.columns

Index(['Unnamed: 0_x', 'correspondence_name', 'Year', 'patents', 'industry',
       'original_name', 'Unnamed: 0_y', 'Infringer', 'troll', 'sued',
       'troll indic', 'sued indic', 'first trolled', 'first sued',
       'Unnamed: 0.1', 'Unnamed: 0', 'Company', 'Currency',
       'Total Assets (millions)', 'Employees (thousands)', 'Company Status',
       'Market Cap (millions)', 'State Incorporated', 'S&P industry code',
       'State', 'Public', 'Always Public'],
      dtype='object')

In [163]:
full_lit_df["first trolled"]# 

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
           ..
7877337   NaN
7877338   NaN
7877339   NaN
7877340   NaN
7877341   NaN
Name: first trolled, Length: 7877342, dtype: float64

In [167]:
len(full_lit_df.loc[(full_lit_df['Always Public'] == 1) & (full_lit_df['first trolled'] > 0), 'correspondence_name'].unique())

164

In [169]:
full_lit_df.head(5)

Unnamed: 0_x         correspondence_name  Year  patents     industry  \
0            22  & bicknell attn: d j brott  2000      0.0  Health Care   
1            23  & bicknell attn: d j brott  2001      0.0  Health Care   
2            24  & bicknell attn: d j brott  2002      0.0  Health Care   
3            25  & bicknell attn: d j brott  2003      0.0  Health Care   
4            26  & bicknell attn: d j brott  2004      0.0  Health Care   

                original_name  Unnamed: 0_y Infringer  troll  sued  ...  \
0  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   
1  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   
2  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   
3  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   
4  & bicknell attn: d j brott           NaN       NaN    NaN   NaN  ...   

   Currency  Total Assets (millions)  Employees (thousands)  Company Status  \
0       NaN                      NaN                    NaN             NaN   
1       NaN                      NaN                    NaN             NaN   
2       NaN                      NaN                    NaN             NaN   
3       NaN                      NaN                    NaN             NaN   
4       NaN                      NaN                    NaN             NaN   

   Market Cap (millions)  State Incorporated S&P industry code State  Public  \
0                    NaN                 NaN               NaN   NaN     NaN   
1                    NaN                 NaN               NaN   NaN     NaN   
2                    NaN                 NaN               NaN   NaN     NaN   
3                    NaN                 NaN               NaN   NaN     NaN   
4                    NaN                 NaN               NaN   NaN     NaN   

   Always Public  
0            NaN  
1            NaN  
2            NaN  
3            NaN  
4            NaN  

[5 rows x 27 columns]

In [4]:
test_look = pd.read_csv("final_merged_all_three.csv")

In [6]:
pd.set_option('display.max_columns', None)
test_look.head(3)

Unnamed: 0         correspondence_name  Year  patents     industry  \
0           0  & bicknell attn: d j brott  2000      0.0  Health Care   
1           1  & bicknell attn: d j brott  2001      0.0  Health Care   
2           2  & bicknell attn: d j brott  2002      0.0  Health Care   

                original_name Infringer  troll  sued  troll indic  sued indic  \
0  & bicknell attn: d j brott       NaN    NaN   NaN          NaN         NaN   
1  & bicknell attn: d j brott       NaN    NaN   NaN          NaN         NaN   
2  & bicknell attn: d j brott       NaN    NaN   NaN          NaN         NaN   

   first trolled  first sued Company Currency  Total Assets (millions)  \
0            NaN         NaN     NaN      NaN                      NaN   
1            NaN         NaN     NaN      NaN                      NaN   
2            NaN         NaN     NaN      NaN                      NaN   

   Employees (thousands) Company Status  Market Cap (millions)  \
0                    NaN            NaN                    NaN   
1                    NaN            NaN                    NaN   
2                    NaN            NaN                    NaN   

  State Incorporated  S&P industry code State  Public  Always Public  gvkey  \
0                NaN                NaN   NaN     NaN            NaN    NaN   
1                NaN                NaN   NaN     NaN            NaN    NaN   
2                NaN                NaN   NaN     NaN            NaN    NaN   

  datadate  fyear indfmt consol popsrc datafmt  tic conm curcd  xrd costat  
0      NaN    NaN    NaN    NaN    NaN     NaN  NaN  NaN   NaN  NaN    NaN  
1      NaN    NaN    NaN    NaN    NaN     NaN  NaN  NaN   NaN  NaN    NaN  
2      NaN    NaN    NaN    NaN    NaN     NaN  NaN  NaN   NaN  NaN    NaN

In [11]:
len(test_look.loc[test_look['Infringer'].isnull() == False])

219976

In [12]:
len(test_look.loc[test_look['Infringer'].isnull() == True])

7657637

In [21]:
test_look.loc[test_look['correspondence_name']== '12 sigma technologies'  ]

Unnamed: 0    correspondence_name  Year  patents  \
3718        3718  12 sigma technologies  2000      0.0   
3719        3719  12 sigma technologies  2001      0.0   
3720        3720  12 sigma technologies  2002      0.0   
3721        3721  12 sigma technologies  2003      0.0   
3722        3722  12 sigma technologies  2004      0.0   
3723        3723  12 sigma technologies  2005      0.0   
3724        3724  12 sigma technologies  2006      0.0   
3725        3725  12 sigma technologies  2007      0.0   
3726        3726  12 sigma technologies  2008      0.0   
3727        3727  12 sigma technologies  2009      0.0   
3728        3728  12 sigma technologies  2010      0.0   
3729        3729  12 sigma technologies  2011      0.0   
3730        3730  12 sigma technologies  2012      0.0   
3731        3731  12 sigma technologies  2013      0.0   
3732        3732  12 sigma technologies  2014      0.0   
3733        3733  12 sigma technologies  2015      0.0   
3734        3734  12 sigma technologies  2016      0.0   
3735        3735  12 sigma technologies  2017      0.0   
3736        3736  12 sigma technologies  2018      0.0   
3737        3737  12 sigma technologies  2019      0.0   
3738        3738  12 sigma technologies  2020      0.0   
3739        3739  12 sigma technologies  2021      0.0   

                    industry          original_name              Infringer  \
3718  Information Technology  12 sigma technologies  12 sigma technologies   
3719  Information Technology  12 sigma technologies  12 sigma technologies   
3720  Information Technology  12 sigma technologies  12 sigma technologies   
3721  Information Technology  12 sigma technologies  12 sigma technologies   
3722  Information Technology  12 sigma technologies  12 sigma technologies   
3723  Information Technology  12 sigma technologies  12 sigma technologies   
3724  Information Technology  12 sigma technologies  12 sigma technologies   
3725  Information Technology  12 sigma technologies  12 sigma technologies   
3726  Information Technology  12 sigma technologies  12 sigma technologies   
3727  Information Technology  12 sigma technologies  12 sigma technologies   
3728  Information Technology  12 sigma technologies  12 sigma technologies   
3729  Information Technology  12 sigma technologies  12 sigma technologies   
3730  Information Technology  12 sigma technologies  12 sigma technologies   
3731  Information Technology  12 sigma technologies  12 sigma technologies   
3732  Information Technology  12 sigma technologies  12 sigma technologies   
3733  Information Technology  12 sigma technologies  12 sigma technologies   
3734  Information Technology  12 sigma technologies  12 sigma technologies   
3735  Information Technology  12 sigma technologies  12 sigma technologies   
3736  Information Technology  12 sigma technologies  12 sigma technologies   
3737  Information Technology  12 sigma technologies  12 sigma technologies   
3738  Information Technology  12 sigma technologies  12 sigma technologies   
3739  Information Technology  12 sigma technologies  12 sigma technologies   

      troll  sued  troll indic  sued indic  first trolled  first sued Company  \
3718    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3719    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3720    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3721    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3722    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3723    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3724    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3725    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3726    0.0   0.0          0.0         0.0         2020.0      2020.0     NaN   
3727    0.0   0.0          0.0         0.0         2020.0      202

In [45]:
test_b =test_look.loc[(test_look['troll']> 0 ) & (test_look['sued']> 0 ) & (test_look['Infringer'].isnull() == False)]

In [47]:
len(test_b.Infringer.unique())

1229

In [39]:
len(test_look.loc[(test_look['troll']> 0 ) & (test_look['sued']> 0 )])

35772

In [37]:
test_a= test_look.loc[(test_look['troll']> 0 ) & (test_look['sued']> 0 ) & (test_look['Company'].isnull() == False)]

In [38]:
len(test_a.Company.unique())

396

In [26]:
len(test_look.loc[(test_look['troll']> 0 ) & (test_look['sued']> 0 )])

35772

In [15]:
len(test_look.loc[test_look['sued']> 0])

152730

In [27]:
len(test_look.loc[test_look['sued'].isnull() == True])

7657637

In [29]:
len(test_look.correspondence_name.unique())

333567

In [32]:
len(test_look.Company.unique())

1059

In [31]:
test_look

Unnamed: 0         correspondence_name  Year  patents  \
0                 0  & bicknell attn: d j brott  2000      0.0   
1                 1  & bicknell attn: d j brott  2001      0.0   
2                 2  & bicknell attn: d j brott  2002      0.0   
3                 3  & bicknell attn: d j brott  2003      0.0   
4                 4  & bicknell attn: d j brott  2004      0.0   
...             ...                         ...   ...      ...   
7877608     7877608                ãyvind berg  2017      0.0   
7877609     7877609                ãyvind berg  2018      0.0   
7877610     7877610                ãyvind berg  2019      0.0   
7877611     7877611                ãyvind berg  2020      0.0   
7877612     7877612                ãyvind berg  2021      0.0   

                 industry               original_name Infringer  troll  sued  \
0             Health Care  & bicknell attn: d j brott       NaN    NaN   NaN   
1             Health Care  & bicknell attn: d j brott       NaN    NaN   NaN   
2             Health Care  & bicknell attn: d j brott       NaN    NaN   NaN   
3             Health Care  & bicknell attn: d j brott       NaN    NaN   NaN   
4             Health Care  & bicknell attn: d j brott       NaN    NaN   NaN   
...                   ...                         ...       ...    ...   ...   
7877608  Consumer Staples                ãyvind berg       NaN    NaN   NaN   
7877609  Consumer Staples                ãyvind berg       NaN    NaN   NaN   
7877610  Consumer Staples                ãyvind berg       NaN    NaN   NaN   
7877611  Consumer Staples                ãyvind berg       NaN    NaN   NaN   
7877612  Consumer Staples                ãyvind berg       NaN    NaN   NaN   

         troll indic  sued indic  first trolled  first sued Company Currency  \
0                NaN         NaN            NaN         NaN     NaN      NaN   
1                NaN         NaN            NaN         NaN     NaN      NaN   
2                NaN         NaN            NaN         NaN     NaN      NaN   
3                NaN         NaN            NaN         NaN     NaN      NaN   
4                NaN         NaN            NaN         NaN     NaN      NaN   
...              ...         ...            ...         ...     ...      ...   
7877608          NaN         NaN            NaN         NaN     NaN      NaN   
7877609          NaN         NaN            NaN         NaN     NaN      NaN   
7877610          NaN         NaN            NaN         NaN     NaN      NaN   
7877611          NaN         NaN            NaN         NaN     NaN      NaN   
7877612          NaN         NaN            NaN         NaN     NaN      NaN   

         Total Assets (millions)  Employees (thousands) Company Status  \
0                            NaN                    NaN            NaN   
1                            NaN                    NaN            NaN   
2                            NaN                    NaN            NaN   
3                            NaN                    NaN            NaN   
4                            NaN                    NaN            NaN   
...                          ...                    ...            ...   
7877608                      NaN                    NaN            NaN   
7877609                      NaN                    NaN            NaN   
7877610                      NaN                    NaN            NaN   
7877611                      NaN                    NaN            NaN   
7877612                      NaN                    NaN            NaN   

         Market Cap (millions) State Incorporated  S&P industry code State  \
0                          NaN                NaN                NaN   NaN   
1                          NaN                NaN                NaN   NaN   
2                          NaN                NaN                NaN   NaN   
3                          NaN                NaN                NaN   NaN   
4              